In [1]:
# Setup

import numpy as np
import math
import matplotlib.pyplot as plt
import sys
import math
import pandas as pd

from bokeh.plotting import figure, show, output_notebook
from bokeh.models import GlyphRenderer, LinearColorMapper, LinearAxis, Range1d
from bokeh.io import push_notebook
#from numba import jit, njit

from ipywidgets import interact

from scipy import optimize

output_notebook()

tools = "hover, box_zoom, undo, crosshair, save, pan, reset, wheel_zoom"

Loading BokehJS ...

In [2]:
# Models

def PolyModel(x, a, b, c):
	return a + (b*x) + (c*x*x)

def LinModel(x, m, c):
	return (m*x)+c

In [3]:
# M & C Calculation

def M_from_ms(arr):
    dep = arr[:,0]
    indep = arr[:,2]
    
    paramsLin, params_covarianceLin = optimize.curve_fit(LinModel, indep, dep)
    return paramsLin
    
def C_from_cs(arr):
    dep = arr[:,1]
    indep = arr[:,2]
    
    paramsLin, params_covarianceLin = optimize.curve_fit(LinModel, indep, dep)
    
    return paramsLin

In [4]:
# m & c Identification for Particular Temp

def hum_for_temp(t, arr, Threshold):
    new_arr = np.array([[0,0,0]])

    for item in arr:
        temper = item[_stemp] - t
        if (abs(temper) < Threshold):
            new_arr = np.append(new_arr,[[item[_vhum],item[_stemp],item[_sraw]]],axis = 0)

    log_dat = new_arr

    vhum  = log_dat[1:,0] #Vaisala Hum,
    stemp = log_dat[1:,1] #Vaisala Hum,
    sraw  = log_dat[1:,2] #SGS RAW,

    #print(log_dat)
    
    paramsLin, params_covarianceLin = optimize.curve_fit(LinModel, vhum, sraw)
    
    p = figure(title="Actual Humidity vs Raw Data at Temp " + str(t), x_axis_label='Vais Hum', y_axis_label='SGS Raw Data')

    p.line(vhum, sraw, legend_label="Data",color="red", line_width=2)
    p.line(vhum, LinModel(vhum,paramsLin[0],paramsLin[1]), legend_label="Model",color="blue", line_width=2)
    #p.line(vhum, LinModel(vhum,arr[5][0],arr[5][1]), legend="Temp " + str(arr[5][2]),color="grey", line_width=2)

    show(p)

    print(paramsLin, t)
    
    paramsLin = np.append(paramsLin, t)
    return paramsLin

In [5]:
# Temp Compensated Humidity Calculation

def calc_hum(Freq, _M, _C, temp):
    M = _M[0]*temp + _M[1]
    C = _C[0]*temp + _C[1]

    Humidity = (Freq - C)/ M
    return Humidity

In [6]:
# Dataset Visualisation

logData2 = pd.read_csv("Dec_ProbeLogs/Log-20-12-2019-12:24.csv") #("Log.csv")#("Log_File_27_Nov.csv")
logData2.head(5)

Time  E+E Hum  E+E Temp  Vaisala Hum  Vaisala Temp  SGS Hum  SGS Temp  \
0  12:24:19        0         0         83.8          14.7    383.9     767.9   
1  12:24:20        0         0         83.8          14.7    383.9     767.9   
2  12:24:21        0         0         83.8          14.7    383.9     767.9   
3  12:24:22        0         0         83.8          14.7    383.9     767.9   
4  12:24:23        0         0         83.8          14.7    383.9     767.9   

   SGS RAW  SGS 2 RevC Hum  SGS 2 RevC Temp  SGS 2 RevC RAW  
0   468781            68.6             14.9          546605  
1   468777            68.6             14.8          546605  
2   468776            68.9             14.8          546601  
3   468772            69.0             14.8          546603  
4   468767            69.0             14.9          546598

In [7]:
# Data Acquisition

log_data2 = logData2.to_numpy()

# Positions in Table
_ehum = 1
_etemp = 2  
_vhum = 3
_vtemp = 4
_shum = 5
_stemp = 4
_sraw = 7
_shum2 = 8
_stemp2 = 9
_sraw2 = 10
#

ehum = log_data2[1:,_ehum]     # E+E Hum,
etemp = log_data2[1:,_ehum]    # E+E Temp,
vhum = log_data2[1:,_vhum] # Vaisala Hum,
vtemp = log_data2[1:,_vtemp] # Vaisala Temp,
stemp = log_data2[1:,_stemp] # SGS Temp,
shum = log_data2[1:,_shum]       # SGS Hum,
sraw = log_data2[1:,_sraw]   # SGS RAW,
stemp2 = log_data2[1:,_stemp2] # SGS Temp,
shum2 = log_data2[1:,_shum2]       # SGS Hum,
sraw2 = log_data2[1:,_sraw2]   # SGS RAW,

sraw = np.array(sraw)   # SGS RAW,

sraw_arr = [] #np.array([0, 1])

count = [ i for i in range(len(vhum) - 1) ]

for el in sraw:
    sraw_arr.append(np.sqrt(el))
    
sraw_freq = np.array(sraw_arr)

data_arr = log_data2[:]

print("Done")

Done


In [8]:
# Model Building : M and C Identification

temps = [10, 20, 30]

new_arr = np.array([ hum_for_temp(temps[0], data_arr, 1.5) ])

for x in range(len(temps)-1):
    new_arr = np.append(new_arr,[hum_for_temp(temps[x+1], data_arr, 1.5)], axis = 0)

colors = ["red", "green", "orange", "blue", "grey", "brown", "purple", "black", "maroon"]
                        
p = figure(title="Actual Humidity vs Raw Data ", x_axis_label='Vais Hum', y_axis_label='SGS Hum')

count1 = -1
for x in new_arr:
    print(x)
    count1 = count1 + 1
    p.line(vhum, LinModel(vhum, x[0], x[1]), legend_label="Temp " + str(x[2]), color=colors[count1], line_width=2)

show(p)

print(new_arr)
print("M : m ", M_from_ms(new_arr)[0], "  c ", M_from_ms(new_arr)[1])
print("C : m ", C_from_cs(new_arr)[0], "  c ", C_from_cs(new_arr)[1])

_M = M_from_ms(new_arr)
_C = C_from_cs(new_arr)

[-3.68943629e+02  5.00778715e+05] 10


[-3.72991338e+02  5.00232145e+05] 20


[-3.62825527e+02  4.99557342e+05] 30
[-3.68943629e+02  5.00778715e+05  1.00000000e+01]
[-3.72991338e+02  5.00232145e+05  2.00000000e+01]
[-3.62825527e+02  4.99557342e+05  3.00000000e+01]


[[-3.68943629e+02  5.00778715e+05  1.00000000e+01]
 [-3.72991338e+02  5.00232145e+05  2.00000000e+01]
 [-3.62825527e+02  4.99557342e+05  3.00000000e+01]]
M : m  0.30590509836968516   c  -374.3715999991324
C : m  -61.068651115841995   c  501410.7733014261


In [9]:
# Data Visualisation

p = figure(title="Actual Humidity vs Raw Data ", x_axis_label='Time (Sec)', y_axis_label='SGS Hum')
p.line(count, data_arr[:,_sraw], legend_label="Data",color="red", line_width=2)
show(p)

p = figure(title="Raw Data", x_axis_label='Time (Sec)', y_axis_label='SGS Hum')
p.line(count, data_arr[:,_sraw2], legend_label="Data",color="red", line_width=2)
show(p)

In [ ]:
# Model Building : M and C Identification

temps = [10, 20, 30]

new_arr = np.array([ hum_for_temp(temps[0], data_arr, 1.5) ])

for x in range(len(temps)-1):
    new_arr = np.append(new_arr,[hum_for_temp(temps[x+1], data_arr, 1.5)], axis = 0)

colors = ["red", "green", "orange", "blue", "grey", "brown", "purple", "black", "maroon"]
                        
p = figure(title="Actual Humidity vs Raw Data ", x_axis_label='Vais Hum', y_axis_label='SGS Hum')

count1 = -1
for x in new_arr:
    print(x)
    count1 = count1 + 1
    p.line(vhum, LinModel(vhum, x[0], x[1]), legend_label="Temp " + str(x[2]), color=colors[count1], line_width=2)

show(p)

print(new_arr)
print("M : m ", M_from_ms(new_arr)[0], "  c ", M_from_ms(new_arr)[1])
print("C : m ", C_from_cs(new_arr)[0], "  c ", C_from_cs(new_arr)[1])

_M = M_from_ms(new_arr)
_C = C_from_cs(new_arr)

In [10]:
# Full Scale Difference

arr = data_arr

new_arr = np.array([[ 0,0,0,0,0,0 ]])

count = -1
for item in arr:
    count = count + 1
    new_arr = np.append(new_arr,[[item[_vhum],
                                  item[_stemp], 
                                  item[_sraw], 
                                  calc_hum(item[_sraw], _M, _C, item[_stemp]),
                                  item[_vhum] - calc_hum(item[_sraw], _M, _C, item[_stemp]),
                                  count
                                 ]], axis = 0 
                       )

log_dat = new_arr

vhum = log_dat[1:,0] 
stemp = log_dat[1:,1] 
sraw = log_dat[1:,2] 
scalc = log_dat[1:,3] 
diff = log_dat[1:,4] 
count = log_dat[1:,5] 

p = figure(title="Calculated Humidity(SGS) vs Vaisala Humidity ", x_axis_label='Vais Hum', y_axis_label='SGS Hum', tools=tools)
p.line(vhum, scalc, line_width=2)
show(p)

# Calc Hum with Vais Humidity with ref to Time

p = figure(title="Calc Humidity with Vais Humidity", x_axis_label='Time (Sec)', y_axis_label='Diff', tools=tools, plot_width=900)
p.line(count, scalc, line_width=1, color="green", legend_label="Calc")
p.line(count, vhum, line_width=1, color="orange", legend_label="Hum")
show(p)

mean_diff = np.mean(diff)
std_dev_diff = np.std(diff)

p = figure(title="Diff bw Vais and SGS, Std Dev: " + str(std_dev_diff), x_axis_label='Vais Hum', y_axis_label='Diff', tools=tools)
p.line(vhum, diff, line_width=2)
show(p)

p = figure(title="Diff bw Vais and SGS", x_axis_label='Temp', y_axis_label='Diff', tools=tools)
p.line(stemp, diff, line_width=2)
show(p)

p = figure(title="Diff bw Vais and SGS", x_axis_label='Time (Sec)', y_axis_label='Diff', tools=tools)
p.line(count, diff, line_width=2)
show(p)

# Diff with Humidity with ref to Time

p.y_range = Range1d(diff.min(), diff.max())
p.extra_y_ranges = {"vhum_range": Range1d(vhum.min(), vhum.max())}

p.add_layout(LinearAxis(y_range_name="vhum_range", axis_label="Humidity"), "right")

p.line(count, diff, line_width=2, color="red", legend_label="Diff")

p.line(count, vhum, line_width=2, color="blue", legend_label="Vaisala Humidity", y_range_name="vhum_range")
show(p)

# Humidity with Temp with ref to Time

p = figure(title="Calc Humidity with Vais Humidity", x_axis_label='Time (Sec)', y_axis_label='Diff', tools=tools, plot_width=900)

p.y_range = Range1d(vhum.min() + 5, vhum.max() + 5)
p.extra_y_ranges = {"stemp_range": Range1d(stemp.min(), stemp.max())}

p.add_layout(LinearAxis(y_range_name="stemp_range", axis_label="Temperature"), "right")

p.line(count, stemp, line_width=0.5, color="red", legend_label="Temp", y_range_name="stemp_range")
p.line(count, scalc, line_width=1, color="green", legend_label="Calc")
p.line(count, vhum, line_width=1, color="orange", legend_label="Hum")
show(p)

In [11]:
# Temp dependent Difference

new_arr = np.array([[0,0,0,0,0]])

temp = 30

arr = data_arr

for item in arr:
    temper = item[6] - temp
    if (abs(temper) < 1.5):
        #print(item)
        new_arr = np.append(new_arr,[[item[3],
                                  item[6], 
                                  item[7], 
                                  calc_hum(item[7], _M, _C, item[6]),
                                  item[3] - calc_hum(item[7], _M, _C, item[6]) 
                                 ]], axis = 0 
                       )
    
vhum = new_arr[1:,0] 
stemp = new_arr[1:,1] 
sraw = new_arr[1:,2] 
scalc = new_arr[1:,3] 
diff = new_arr[1:,4] 

p = figure(title="Calculated Humidity vs Vaisala Humidity at Temp " + str(temp), x_axis_label='Vais Hum', y_axis_label='SGS Hum')
p.line(vhum, scalc, line_width=2)
show(p)

std_diff = np.std(diff)

p = figure(title="Diff bw Vais and SGS, Std Dev: " + str(std_diff), x_axis_label='Vais Hum', y_axis_label='Difference')
p.line(vhum, diff, line_width=2)
show(p)

/usr/local/lib/python3.6/dist-packages/numpy/core/_methods.py:140: RuntimeWarning: Degrees of freedom <= 0 for slice
  keepdims=keepdims)
/usr/local/lib/python3.6/dist-packages/numpy/core/_methods.py:110: RuntimeWarning: invalid value encountered in true_divide
  arrmean, rcount, out=arrmean, casting='unsafe', subok=False)
/usr/local/lib/python3.6/dist-packages/numpy/core/_methods.py:132: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


In [12]:
# Hum & Temp Variation Visualisation

new_arr = np.array([[0,0,0,0,0,0]])

arr = data_arr

count = -1
for item in arr:
    count = count + 1
    new_arr = np.append(new_arr,[[item[_vhum],
                                  item[_stemp], 
                                  item[_sraw], 
                                  calc_hum(item[_vhum], _M, _C, item[]),
                                  abs(item[3] - calc_hum(item[_vhum], _M, _C, item[])),
                                  count
                                 ]], axis = 0 
                       )
    
vhum = new_arr[1:,0] #Vaisala Hum,
stemp = new_arr[1:,1] #Vaisala Hum,
sraw = new_arr[1:,2] #SGS RAW,
scalc = new_arr[1:,3] #SGS RAW,
diff = new_arr[1:,4] #SGS RAW,
count = new_arr[1:,5] #SGS RAW,

p = figure(title="Temp and Humidity Variation", x_axis_label='Time(sec)', y_axis_label='Temperature', plot_width=900)

p.y_range = Range1d(stemp.min(), stemp.max())
p.extra_y_ranges = {"vhum_range": Range1d(vhum.min(), vhum.max())}

p.add_layout(LinearAxis(y_range_name="vhum_range", axis_label="Humidity"), "right")

p.line(count, stemp, name="Data", line_width=2, color="red", legend_label="Temp")

p.line(count, vhum, name="Data", line_width=2, color="blue", legend_label="Vaisala Humidity", y_range_name="vhum_range")

show(p)

SyntaxError: invalid syntax (<ipython-input-12-ba6fc79568a0>, line 13)

In [ ]:
new_arr = np.array([[0,0,0,0]])

arr = data_arr

count = -1
for item in arr:
    count = count + 1
    new_arr = np.append(new_arr,[[item[3],item[6],item[7], count]],axis = 0)
    
vhum = new_arr[1:,0] #Vaisala Hum,
stemp = new_arr[1:,1] #Vaisala Hum,
sraw = new_arr[1:,2] #SGS RAW,
count = new_arr[1:,3] #SGS RAW,

paramsLin, params_covarianceLin = optimize.curve_fit(LinModel, vhum, sraw)

print(paramsLin)

p = figure(title="Raw Data and Humidity Variation", x_axis_label='Time(sec)', y_axis_label='Raw')

p.y_range = Range1d(sraw.min(), sraw.max())
p.extra_y_ranges = {"vhum_range": Range1d(vhum.min(), vhum.max())}
p.add_layout(LinearAxis(y_range_name="vhum_range"), "right")

p.line(count, sraw, name="Data", line_width=2, color="red", legend="Raw")

p.line(count, vhum, name="Data", line_width=2, color="blue", legend="Vaisala Humidity", y_range_name="vhum_range")

show(p)

#p = figure(title="At Temp " + str(temp), x_axis_label='Time', y_axis_label='Raw')
#p.line(count, vhum, name="Data", line_width=2, color="red", legend="Raw")
#show(p)